In [4]:
import streamlit as st
from pyvis.network import Network
import pandas as pd
import streamlit.components.v1 as components
from db_info import user, password, host, database, port
import mysql.connector
import plotly.express as px
import plotly.graph_objects as go


# MySQL 데이터베이스 연결
db_connection = mysql.connector.connect(
    host=host,
    user=user,
    password=password,
    database=database,
    port=port
)

cursor = db_connection.cursor()

# 데이터 가져오기
cursor.execute("SELECT 판례일련번호,사건번호,클러스터,판례내용_이유 FROM inheritance_keyword")
result = cursor.fetchall()

# DataFrame 생성 및 컬럼 이름 설정
df_inheritance = pd.DataFrame(result, columns=[i[0] for i in cursor.description])

In [5]:
df_inheritance.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4127 entries, 0 to 4126
Data columns (total 4 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   판례일련번호   4127 non-null   int64 
 1   사건번호     4127 non-null   object
 2   클러스터     4127 non-null   int64 
 3   판례내용_이유  4127 non-null   object
dtypes: int64(2), object(2)
memory usage: 129.1+ KB


In [80]:
df_inheritance.to_csv('저장저장.csv')

In [8]:
df_inheritance['판례내용_이유'].iloc[1000]

'【이    유】1. 처분의 경위  가. 한국토지주택공사는 국방·군사시설사업에 관한 법률에 따른 국방·군사시설사업인 ◇◇◇◇◇◇ 및 ☆☆☆☆☆☆☆☆ 이전사업(이하 ‘이 사건 사업’이라 한다)의 사업시행자이다.  나. 이천시 (주소 생략) 전 1,319㎡(이하 ‘이 사건 토지’라 한다)에 관하여 1956. 6. 30. 수원지방법원 이천등기소 접수 제750호로 피고보조참가인(이하 ‘참가인’이라고만 한다) 명의의 소유권보존등기(이하 ‘이 사건 보존등기’라 한다)가 마쳐져 있었는데, 한국토지주택공사는 2009. 8. 6. 이 사건 사업의 부지에 포함된 이 사건 토지를 취득하기 위하여 그 등기명의자였던 참가인과 사이에 협의를 성립시키고(이하 ‘이 사건 협의’라 한다), 2009. 8. 26. 이를 원인으로 한 소유권이전등기(이하 ‘이 사건 이전등기’라 한다)를 마쳤다.  다. 원고는 2014. 10. 10. 서울중앙지방법원 2014가단209928호로 원고의 부(父)인 소외 1(대판: 소외인)로부터 이 사건 토지를 상속한 자신이 이 사건 토지의 진정한 소유자라고 주장하며 참가인과 한국토지주택공사를 상대로 이 사건 보존등기 및 이 사건 이전등기의 말소를 구하는 소를 제기하였다.  라. 이후 한국토지주택공사는 「공익사업을 위한 토지 등의 취득 및 보상에 관한 법률」(이하 ‘토지보상법’이라 한다) 제29조에 따라 이 사건 토지의 소유자로서 참가인의 동의를 받고 한국주택공사와 참가인 사이의 매매계약서, 협의성립확인신청 동의서, 토지조서 및 보상금지급서류에 공증을 받아 피고에게 이 사건 토지에 관한 협의 성립의 확인을 신청하였고, 피고는 2015. 3. 26. 별지1 기재와 같이 이를 수리하였다(이하 ‘이 사건 처분’이라 한다).  마. 한편, 소외 1에게는 처 소외 2, 1남 소외 3, 2남 소외 4, 3남 소외 5, 4남 원고, 5남 소외 6, 1녀 소외 7, 2녀 소외 8이 있었고, 소외 1은 1959. 9. 29. 사망하였는데, 사망 당시 이미 1남 소외 3는 1925. 

In [43]:
import pandas as pd
import re


# '판결한다.' 뒤에 나오는 텍스트를 추출하는 함수
def extract_text_after_judgement(text):
    match = re.search(r'판결한다\.(.*)', text)
    if match:
        return match.group(1).strip()  # '판결한다.' 뒤의 텍스트
    return None  # '판결한다.'이 없으면 None 반환

# '판결한다.'가 있으면 '판결 뒤 텍스트'에 담고, 없으면 '없는거'에 담기
def separate_text(text):
    if '판결한다.' in text:
        return extract_text_after_judgement(text), None  # 판결 뒤 텍스트, '없는거'는 None
    return None, text  # '판결한다.'가 없으면 '없는거'에 원문 텍스트

# '판결 뒤 텍스트'와 '없는거' 칼럼을 추가
df_new = df_inheritance.copy()
df_new ['판결 뒤 텍스트'], df_new ['없는거'] = zip(*df_new ['판례내용_이유'].apply(separate_text))


In [44]:
df_new.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4127 entries, 0 to 4126
Data columns (total 6 columns):
 #   Column    Non-Null Count  Dtype 
---  ------    --------------  ----- 
 0   판례일련번호    4127 non-null   int64 
 1   사건번호      4127 non-null   object
 2   클러스터      4127 non-null   int64 
 3   판례내용_이유   4127 non-null   object
 4   판결 뒤 텍스트  3650 non-null   object
 5   없는거       477 non-null    object
dtypes: int64(2), object(4)
memory usage: 193.6+ KB


In [45]:
df_new['없는거'].unique()

array([None,
       '【이    유】  1. 처분의 경위  가. 당사자의 지위 등 소외 2는 2013. 10. 17. 유언을 남기지 않고 사망하였다(이하 소외 2를 ‘고인’이라 한다). 소외 1은 고인의 아내이고, 원고 1, 원고 2는 고인의 자녀들이다.  나. 상속세의 신고·부과 등 경과   1) 원고 1, 원고 2와 소외 1(이하 이들을 한꺼번에 표시할 경우 ‘원고 1 등’이라 한다)은 2014. 4. 30. 상속세를 신고하였다. 원고 1 등은 고인이 남긴 별지 1 목록 기재 부동산들(이하 ‘이 사건 부동산’이라 한다)과 정기예탁금 등에 대하여 총 상속재산가액을 16,875,817,600원으로 산정하고, 구 상속세 및 증여세법(2016. 12. 20. 법률 제14388호로 일부 개정되기 전의 것, 이하 ‘구 상증세법’이라 한다) 제19조에 따른 배우자 상속공제로 30억 원을 공제하는 등의 과정을 거쳐 세액을 5,413,106,333원으로 계산해 제출하였다.  2) 당시 원고 1 등은 상속재산 전체를 원고 1 등이 공동으로 상속한 것으로 보아, 각 상속인별로 상속재산명세서를 작성하였다. 원고 1 등은 2014. 6. 5. 이 사건 부동산 중 상속재산 분할과 관련하여 이견이 있던 일부 부동산을 제외한 토지 24필지와 건물 1동에 대하여 법정상속분에 따라 소외 1 3/7, 원고 1·원고 2 각 2/7씩의 비율로 상속등기를 마쳤다.   3) 원고 1 등은 2014. 7. 22. 위와 같이 신고한 상속세에 대하여 연부연납허가신청을 하였고, 피고는 2014. 10. 16. 이를 허가하였다.   4) 피고는 원고 1 등이 신고한 상속세 신고내역과 고인의 사전증여 여부 등에 대하여 2014. 10. 30.~2015. 7. 6. 사이에 조사를 실시한 다음, 2015. 7. 23. 원고 1 등에게 추가로 616,298,022원의 상속세를 부과하였다. 원고 1 등은 2015. 8. 31.까지 위와 같이 신고·부과된 상속세를 모두 납부하였다.  다. 상속재산 분

In [66]:
def extract_last_100_chars(text):
    if text is None:
        return None
    return text[-100:]  # 뒤에서부터 100글자 추출

# 새로운 칼럼 '뒤에서 100글자' 추가
df_new['뒤에서 100글자'] = df_new['없는거'].apply(extract_last_100_chars)

In [67]:
df_new.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4127 entries, 0 to 4126
Data columns (total 11 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   판례일련번호     4127 non-null   int64 
 1   사건번호       4127 non-null   object
 2   클러스터       4127 non-null   int64 
 3   판례내용_이유    4127 non-null   object
 4   판결 뒤 텍스트   3650 non-null   object
 5   없는거        477 non-null    object
 6   재판장 앞 4글자  2 non-null      object
 7   재판장 앞 3글자  2 non-null      object
 8   재판장 이름만    2 non-null      object
 9   대법관 뒤 텍스트  122 non-null    object
 10  뒤에서 100글자  477 non-null    object
dtypes: int64(2), object(9)
memory usage: 354.8+ KB


In [68]:
df_new['뒤에서 100글자'].unique()

array([None,
       ' 한다. 제1심판결은 이와 결론이 같다. 그러므로 원고들의 항소를 모두 기각하기로 한다.[별 지 1] 목록: 생략[별 지 2] 관계 법령: 생략판사 조찬영(재판장) 김무신 김승주 ',
       '하지 않다.  이상과 같이 다수의견에 대한 보충의견을 밝힌다.대법원장 김명수(재판장) 조재연 박정화 안철상 민유숙(주심) 김선수 이동원 노정희 노태악 이흥구 천대엽 오경미 오석준 ',
       '결정을 파기하고, 사건을 다시 심리·판단하도록 원심법원에 환송하기로 하여, 관여 대법관의 일치된 의견으로 주문과 같이 결정한다.대법관 천대엽(재판장) 조재연 민유숙(주심) 이동원 ',
       ' 부분 사건을 다시 심리·판단하게 하기 위하여 원심법원에 환송하기로 하여, 관여 대법관의 일치된 의견으로 주문과 같이 결정한다.대법관 김선수(재판장) 박정화 노태악 오경미(주심) ',
       '.  이상과 같은 이유로 다수의견에 찬성할 수 없음을 밝힌다.대법원장 김명수(재판장) 조희대(주심) 권순일 박상옥 이기택 김재형 박정화 안철상 민유숙 김선수 이동원 노정희 김상환 ',
       '이유 없어 기각하기로 하여 주문과 같이 판결한다(소송총비용은 원고들 패소부분이 극히 근소하여 피고가 전부 부담하는 것으로 정한다).[별지 생략]판사 최병률(재판장) 임재남 공민아 ',
       '.  그러므로 재항고를 모두 기각하고, 재항고비용은 패소자들이 부담하기로 하여, 대법관의 일치된 의견으로 주문과 같이 결정한다.대법관 이동원(재판장) 조희대 김재형(주심) 민유숙 ',
       '청구인 겸 반심판상대방) 4, 상대방(반심판청구인 겸 반심판상대방) 5의 나머지 항고를 각 기각하기로 하여, 주문과 같이 결정한다.[별지 생략]판사 김용대(재판장) 류재훈 박정운 ',
       ' 부분은 정당하므로 상대방 1의 이 사건 반심판 기여분 결정 청구 부분에 대한 항고는 이를 기각하기로 하여 주문과 같이 결정한다. [별지 생략]판사 정용달(재판장)

In [69]:
# '(재판장)' 뒤의 텍스트를 삭제하는 함수
def remove_text_after_judge(text):
    if text is None:
        return None
    # '(재판장)' 뒤의 모든 텍스트를 삭제
    return re.sub(r'\(재판장\).*', '(재판장)', text)

# 새로운 칼럼 '재판장 뒤 텍스트 삭제' 추가
df_new['재판장 뒤 텍스트 삭제'] = df_new['뒤에서 100글자'].apply(remove_text_after_judge)

In [70]:
df_new['재판장 뒤 텍스트 삭제'].unique()

array([None,
       ' 한다. 제1심판결은 이와 결론이 같다. 그러므로 원고들의 항소를 모두 기각하기로 한다.[별 지 1] 목록: 생략[별 지 2] 관계 법령: 생략판사 조찬영(재판장)',
       '하지 않다.  이상과 같이 다수의견에 대한 보충의견을 밝힌다.대법원장 김명수(재판장)',
       '결정을 파기하고, 사건을 다시 심리·판단하도록 원심법원에 환송하기로 하여, 관여 대법관의 일치된 의견으로 주문과 같이 결정한다.대법관 천대엽(재판장)',
       ' 부분 사건을 다시 심리·판단하게 하기 위하여 원심법원에 환송하기로 하여, 관여 대법관의 일치된 의견으로 주문과 같이 결정한다.대법관 김선수(재판장)',
       '.  이상과 같은 이유로 다수의견에 찬성할 수 없음을 밝힌다.대법원장 김명수(재판장)',
       '이유 없어 기각하기로 하여 주문과 같이 판결한다(소송총비용은 원고들 패소부분이 극히 근소하여 피고가 전부 부담하는 것으로 정한다).[별지 생략]판사 최병률(재판장)',
       '.  그러므로 재항고를 모두 기각하고, 재항고비용은 패소자들이 부담하기로 하여, 대법관의 일치된 의견으로 주문과 같이 결정한다.대법관 이동원(재판장)',
       '청구인 겸 반심판상대방) 4, 상대방(반심판청구인 겸 반심판상대방) 5의 나머지 항고를 각 기각하기로 하여, 주문과 같이 결정한다.[별지 생략]판사 김용대(재판장)',
       ' 부분은 정당하므로 상대방 1의 이 사건 반심판 기여분 결정 청구 부분에 대한 항고는 이를 기각하기로 하여 주문과 같이 결정한다. [별지 생략]판사 정용달(재판장)',
       '없다.      결국 원고들의 위 주장은 받아들일 수 없다.3. 결 론   제1심 판결은 정당하다. 원고들의 항소를 모두 기각한다.[별지 생략]판사 김용빈(재판장)',
       '  그렇다면 이 사건 기여분결정 청구 및 상속재산분할 청구에 관하여 위와 같이 정하기로 하여 주문과 같이 심판한다.[[별   지

In [77]:
# '(재판장)' 앞의 4글자만 남기고 그 앞은 삭제하는 함수
def keep_last_4_chars_before_judge(text):
    if text is None:
        return None
    # '(재판장)' 앞 4글자만 남기고 그 앞은 모두 삭제
    match = re.search(r'.*(.{4})\(재판장\)', text)
    if match:
        return match.group(1) + '(재판장)'  # 4글자 + (재판장) 반환
    return None  # '(재판장)'이 없으면 None 반환

# '(재판장)'이 있을 경우 4글자만 남기고 삭제
df_new['4글자만 남기고 삭제'] = df_new['재판장 뒤 텍스트 삭제'].apply(keep_last_4_chars_before_judge)

# '(재판장)'이 없으면
df_no_judge = df_new[df_new['4글자만 남기고 삭제'].isnull()]

In [78]:
df_new['4글자만 남기고 삭제'].info()

<class 'pandas.core.series.Series'>
RangeIndex: 4127 entries, 0 to 4126
Series name: 4글자만 남기고 삭제
Non-Null Count  Dtype 
--------------  ----- 
406 non-null    object
dtypes: object(1)
memory usage: 32.4+ KB


In [79]:
df_no_judge.info()

<class 'pandas.core.frame.DataFrame'>
Index: 3721 entries, 0 to 4126
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   판례일련번호        3721 non-null   int64 
 1   사건번호          3721 non-null   object
 2   클러스터          3721 non-null   int64 
 3   판례내용_이유       3721 non-null   object
 4   판결 뒤 텍스트      3650 non-null   object
 5   없는거           71 non-null     object
 6   재판장 앞 4글자     2 non-null      object
 7   재판장 앞 3글자     2 non-null      object
 8   재판장 이름만       2 non-null      object
 9   대법관 뒤 텍스트     0 non-null      object
 10  뒤에서 100글자     71 non-null     object
 11  재판장 뒤 텍스트 삭제  71 non-null     object
 12  4글자만 남기고 삭제   0 non-null      object
dtypes: int64(2), object(11)
memory usage: 407.0+ KB


In [73]:
df_new['4글자만 남기고 삭제'].unique()

array([None, ' 조찬영(재판장)', ' 김명수(재판장)', ' 천대엽(재판장)', ' 김선수(재판장)',
       ' 최병률(재판장)', ' 이동원(재판장)', ' 김용대(재판장)', ' 정용달(재판장)', ' 김용빈(재판장)',
       ' 문준섭(재판장)', ' 조희대(재판장)', ' 배인구(재판장)', ' 안철상(재판장)', ' 김용덕(재판장)',
       '관 김신(재판장)', ' 김용석(재판장)', ' 최규홍(재판장)',
       '이 사건 청구는 위 인정 범위 내에서 이유 있어 인용하고 나머지 청구는 기각한다. 소송비용은 소송경위, 승패결과 등에 비추어 각자 부담하는 것으로 정한다.(별지 생략)판사 서영효 ',
       ' 김상준(재판장)', ' 김선일(재판장)', ' 고영한(재판장)', ' 박종택(재판장)', ' 김인욱(재판장)',
       ' 이일주(재판장)', ' 이상훈(재판장)', ' 김창종(재판장)', ' 임채웅(재판장)', ' 김지형(재판장)',
       ' 문형배(재판장)', ' 차한성(재판장)', ' 최우식(재판장)', '사 김신(재판장)', ' 고현철(재판장)',
       ' 김홍우(재판장)', ' 김용담(재판장)', ' 김용헌(재판장)', ' 김선종(재판장)', ' 김창섭(재판장)',
       ' 조무제(재판장)',
       '실하다 보기 어려워, 위 협의분할이 피고들의 상속포기에 반하는 처분이라고 할 수 없다.  3. 결론  그렇다면 원고의 이 사건 청구는 이유 없으므로, 이를 기각한다. 판사 배인구 ',
       ' 황정규(재판장)', ' 지영철(재판장)', ' 유지담(재판장)', ' 고의영(재판장)', ' 이규홍(재판장)',
       ' 윤재식(재판장)', ' 김형선(재판장)', ' 이돈희(재판장)', ' 이용훈(재판장)', ' 전봉진(재판장)',
       ' 황우여(재판장)', ' 이재성(재판장)', ' 이회창(재판장)', ' 안우만(재판장)', ' 이준승(재판장)',